<a href="https://colab.research.google.com/github/MarioCastilloM/Activos_Derivados/blob/main/Tarea_Portafolio.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<img style="float: right;" align="center" src="https://www.udp.cl/cms/wp-content/uploads/2021/06/UDP_LogoRGB_2lineas_Color_SinFondo.png">

# Tarea Portafolio

<!-- ![picture](https://www.udp.cl/cms/wp-content/uploads/2021/06/UDP_LogoRGB_2lineas_Color_SinFondo.png) -->

## Integrantes

-  Mario Castillo
-  Felipe Gálvez

In [111]:
!pip install yfinance

In [112]:
class Portfolio:

  from datetime import date
  def __init__(self, df = None, ticker = None, start = date(2010, 1, 1), end = date.today(), rf = 0.05, J = 10000):
    self.df = df if df is not None else ticker
    self.start = start
    self.end = end
    self.rf = rf
    self.J = J
  
  def _prepare_data(self):
    import pandas as pd
    import yfinance as yf
    if isinstance(self.df, pd.DataFrame):
      self.df.iloc[:, 1:] = self.df.iloc[:, 1:].pct_change()
      df = self.df.dropna()
      df.set_index('Date', inplace = True)
    else:
      data = [yf.download(x, start=self.start, end=self.end, progress=False) for x in self.df]
      for i in range(len(data)):
        data[i]['ticker'] = self.df[i]
      df = pd.concat(data)
    df = (df.reset_index().pivot(index='Date',columns="ticker", values="Adj Close").sort_index(level=[1,0]))
    df = df.pct_change()
    df.dropna(inplace = True)
    return df
  
  def _portfolio_sim(self, df):
    import pandas as pd
    import numpy as np
    n = self.J
    m = len(df.columns)
    matrix = np.zeros((n, m))
    p_ret = np.zeros(n)
    p_risk = np.zeros(n)
    sharpe = np.zeros(n)
    cov = df.cov()
    avg_ret = df.apply(np.mean, axis = 0)
    for i in range(n):
      w = np.random.uniform(size = m)
      w = w/np.sum(w)
      matrix[i, :] = w
      ret = np.sum(w * avg_ret)
      ret = ((ret + 1)**252) - 1
      p_ret[i] = ret
      risk = (w.T@cov@w)**0.5
      p_risk[i] = risk
      s = (ret - self.rf) / risk
      sharpe[i] = s
    portfolio_values = pd.DataFrame({
        'Retorno': p_ret,
        'Riesgo': p_risk,
        'Sharpe Ratio': sharpe
    })
    matrix = pd.DataFrame(matrix, 
                          columns = df.columns)
    portfolio_values = pd.concat([portfolio_values.reset_index(drop=True), matrix], axis=1)
    min_var = portfolio_values[portfolio_values['Riesgo'] == np.min(portfolio_values['Riesgo'])]
    max_ret = portfolio_values[portfolio_values['Retorno'] == np.max(portfolio_values['Retorno'])]
    max_sharpe = portfolio_values[portfolio_values['Sharpe Ratio'] == np.max(portfolio_values['Sharpe Ratio'])]
    min_max = min_var.append(max_ret).append(max_sharpe).reset_index(drop = True).rename(index = {
        0: 'Min Var',
        1: 'Max Ret',
        2: 'Tangente'
        })
    return min_max, portfolio_values

  def efficient_frontier(self, df, min_max_df):
    import plotly.express as px
    import plotly.graph_objects as go
    fig = px.scatter(df, x = "Riesgo", y = "Retorno", color = "Sharpe Ratio", hover_data = ['Sharpe Ratio'],
                     color_continuous_scale=px.colors.sequential.Viridis,
                     title = "Eficient Frontier")
    fig.add_trace(go.Scatter(x = [min_max.loc['Tangente']['Riesgo']], 
                             y = [min_max.loc['Tangente']['Retorno']], 
                             mode = 'markers', name = 'Optimal Portfolio', 
                             marker = dict(size = [30], color = 'yellow')))
    fig.add_trace(go.Scatter(x = [min_max.loc['Min Var']['Riesgo']], 
                             y = [min_max.loc['Min Var']['Retorno']], 
                             mode = 'markers', name = 'Min Risk Portfolio', 
                             marker = dict(size = [30], color = 'navy')))
    fig.update_layout(coloraxis_colorbar = dict(
        title = 'Sharpe Ratio',
        thicknessmode = 'pixels', thickness = 25,
        lenmode = 'pixels',
        yanchor = 'middle', y = 0.4,
        dtick = 5
    ))
    return fig

  def investment_growth(self, df, weights):
    import plotly.express as px
    import numpy as np
    import pandas as pd
    ini_inv = 10000
    a = (weights.loc['Tangente'][3:] * df.iloc[1:]).apply(sum, axis = 1)
    x = np.zeros(len(a))
    for i in range(1, len(a)):
      x[0] = 10000
      x[i] = x[i-1] * (1+a[i-1])
    df_ = pd.DataFrame({"Date": a.index,
                        "Inversión": x})
    fig = px.line(df_, x = "Date", y = "Inversión",
                     title = "Investment Growth")
    return fig, df_
  
  def portfolio_composition(self, min_max):
    import pandas as pd
    import plotly.express as px
    x = input('Selecciona una opción ("Min Var", "Max Ret", "Tangente"): ')
    port = min_max.loc[x,:][3:]
    p = pd.DataFrame(port).sort_values(by = [x]).reset_index().rename(columns = {"index": "Stock"})
    p1 = px.bar(p, x="Stock", y=x, color="Stock", title= p.columns[1] + " Portfolio Composition")
    return p1

In [113]:
a = Portfolio(ticker=['TSLA', 'AMZN', 'AAPL', '^GSPC', '000001.SS'], J = 100000)
b = a._prepare_data()

In [114]:
min_max, simulation = a._portfolio_sim(b)

In [115]:
a.efficient_frontier(simulation, min_max)

In [116]:
figura, data = a.investment_growth(b, min_max)

In [117]:
figura.show()

In [118]:
# Ingresa Tangente al input solicitado en consola

a.portfolio_composition(min_max)

Selecciona una opción ("Min Var", "Max Ret", "Tangente"): Tangente


In [119]:
# Ingresa Min Var al input solicitado en consola

a.portfolio_composition(min_max)

Selecciona una opción ("Min Var", "Max Ret", "Tangente"): Min Var


In [120]:
# Ingresa Max Ret al input solicitado en consola

a.portfolio_composition(min_max)

Selecciona una opción ("Min Var", "Max Ret", "Tangente"): Max Ret
